# Setup

In [127]:
from _ctypes import LoadLibrary as _dlopen
_dlopen("D:\\Sangwons_Room\\00_SoftWares\\Anaconda\\envs\\torch\\Library\\bin\\geos.dll", 0)

140703397314560

In [128]:

# nuscenes-devkit
from nuscenes.nuscenes import NuScenes

# nuscenes-map expansion
from nuscenes.map_expansion.map_api import NuScenesMap
from nuscenes.map_expansion import arcline_path_utils
from nuscenes.map_expansion.bitmap import BitMap

# nuscenes-devkit-utils
from nuscenes.utils.data_classes import LidarPointCloud, RadarPointCloud, Box
from nuscenes.utils.geometry_utils import view_points, transform_matrix

from pyquaternion import Quaternion


from functools import reduce
import os

import numpy as np
import matplotlib.pyplot as plt
import plotly.express as px
import tqdm
%matplotlib inline

In [2]:
nusc = NuScenes(version='v1.0-mini', dataroot='./data/sets/nuscenes', verbose=True)

nusc_map = NuScenesMap(dataroot='./data/sets/nuscenes', map_name='singapore-onenorth')

Loading NuScenes tables for version v1.0-mini...
Loading nuScenes-lidarseg...
32 category,
8 attribute,
4 visibility,
911 instance,
12 sensor,
120 calibrated_sensor,
31206 ego_pose,
8 log,
10 scene,
404 sample,
31206 sample_data,
18538 sample_annotation,
4 map,
404 lidarseg,
Done loading in 0.620 seconds.
Reverse indexing ...
Done reverse indexing in 0.1 seconds.


# Get One Sample

In [134]:
nusc.list_scenes()

scene-0061, Parked truck, construction, intersectio... [18-07-24 03:28:47]   19s, singapore-onenorth, #anns:4622
scene-0103, Many peds right, wait for turning car, ... [18-08-01 19:26:43]   19s, boston-seaport, #anns:2046
scene-0655, Parking lot, parked cars, jaywalker, be... [18-08-27 15:51:32]   20s, boston-seaport, #anns:2332
scene-0553, Wait at intersection, bicycle, large tr... [18-08-28 20:48:16]   20s, boston-seaport, #anns:1950
scene-0757, Arrive at busy intersection, bus, wait ... [18-08-30 19:25:08]   20s, boston-seaport, #anns:592
scene-0796, Scooter, peds on sidewalk, bus, cars, t... [18-10-02 02:52:24]   20s, singapore-queensto, #anns:708
scene-0916, Parking lot, bicycle rack, parked bicyc... [18-10-08 07:37:13]   20s, singapore-queensto, #anns:2387
scene-1077, Night, big street, bus stop, high speed... [18-11-21 11:39:27]   20s, singapore-hollandv, #anns:890
scene-1094, Night, after rain, many peds, PMD, ped ... [18-11-21 11:47:27]   19s, singapore-hollandv, #anns:1762
sc

In [7]:
my_scene = nusc.scene[0]
first_sample_token = my_scene['first_sample_token']
my_scene

{'token': 'cc8c0bf57f984915a77078b10eb33198',
 'log_token': '7e25a2c8ea1f41c5b0da1e69ecfa71a2',
 'nbr_samples': 39,
 'first_sample_token': 'ca9a282c9e77460f8360f564131a8af5',
 'last_sample_token': 'ed5fc18c31904f96a8f0dbb99ff069c0',
 'name': 'scene-0061',
 'description': 'Parked truck, construction, intersection, turn left, following a van'}

In [8]:
my_sample = nusc.get('sample', first_sample_token)
my_sample

{'token': 'ca9a282c9e77460f8360f564131a8af5',
 'timestamp': 1532402927647951,
 'prev': '',
 'next': '39586f9d59004284a7114a68825e8eec',
 'scene_token': 'cc8c0bf57f984915a77078b10eb33198',
 'data': {'RADAR_FRONT': '37091c75b9704e0daa829ba56dfa0906',
  'RADAR_FRONT_LEFT': '11946c1461d14016a322916157da3c7d',
  'RADAR_FRONT_RIGHT': '491209956ee3435a9ec173dad3aaf58b',
  'RADAR_BACK_LEFT': '312aa38d0e3e4f01b3124c523e6f9776',
  'RADAR_BACK_RIGHT': '07b30d5eb6104e79be58eadf94382bc1',
  'LIDAR_TOP': '9d9bf11fb0e144c8b446d54a8a00184f',
  'CAM_FRONT': 'e3d495d4ac534d54b321f50006683844',
  'CAM_FRONT_RIGHT': 'aac7867ebf4f446395d29fbd60b63b3b',
  'CAM_BACK_RIGHT': '79dbb4460a6b40f49f9c150cb118247e',
  'CAM_BACK': '03bea5763f0f4722933508d5999c5fd8',
  'CAM_BACK_LEFT': '43893a033f9c46d4a51b5e08a67a1eb7',
  'CAM_FRONT_LEFT': 'fe5422747a7d4268a4b07fc396707b23'},
 'anns': ['ef63a697930c4b20a6b9791f423351da',
  '6b89da9bf1f84fd6a5fbe1c3b236f809',
  '924ee6ac1fed440a9d9e3720aac635a0',
  '91e3608f55174a319

In [12]:
lidar_top_data = nusc.get('sample_data', my_sample['data']['LIDAR_TOP'])
pcl_path = os.path.join(nusc.dataroot, lidar_top_data['filename'])

pc = LidarPointCloud.from_file(pcl_path)
print(pc.points.shape)

(4, 34688)


In [37]:
fig = px.scatter_3d(x = pc.points[0,:], y = pc.points[1,:], z = pc.points[2,:], size = np.ones_like(pc.points[0,:]) * 0.3, 
                    size_max = 2, range_x = [-100, 100], range_y = [-100, 100], range_z = [-100, 100],
                   width = 800, height = 500)

fig.show()

In [45]:
lidar_top_data

{'token': '9d9bf11fb0e144c8b446d54a8a00184f',
 'sample_token': 'ca9a282c9e77460f8360f564131a8af5',
 'ego_pose_token': '9d9bf11fb0e144c8b446d54a8a00184f',
 'calibrated_sensor_token': 'a183049901c24361a6b0b11b8013137c',
 'timestamp': 1532402927647951,
 'fileformat': 'pcd',
 'is_key_frame': True,
 'height': 0,
 'width': 0,
 'filename': 'samples/LIDAR_TOP/n015-2018-07-24-11-22-45+0800__LIDAR_TOP__1532402927647951.pcd.bin',
 'prev': '',
 'next': '0cedf1d2d652468d92d23491136b5d15',
 'sensor_modality': 'lidar',
 'channel': 'LIDAR_TOP'}

# Scene

In [44]:
my_sample['data']['LIDAR_TOP']

'9d9bf11fb0e144c8b446d54a8a00184f'

In [46]:
my_scene = nusc.scene[0]
first_sample_token = my_scene['first_sample_token']
last_sample_token = my_scene['last_sample_token']

token = first_sample_token
count = 0
while(token != last_sample_token):
    my_sample = nusc.get('sample', token)
    
    lidar_top_data = nusc.get('sample_data', my_sample['data']['LIDAR_TOP'])
    pcl_path = os.path.join(nusc.dataroot, lidar_top_data['filename'])

    pc = LidarPointCloud.from_file(pcl_path)
    print(pc.points.shape)

    token = my_sample['next']
    count+=1
    print(count, token)


(4, 34688)
1 39586f9d59004284a7114a68825e8eec
(4, 34720)
2 356d81f38dd9473ba590f39e266f54e5
(4, 34720)
3 e0845f5322254dafadbbed75aaa07969
(4, 34688)
4 c923fe08b2ff4e27975d2bf30934383b
(4, 34752)
5 f1e3d9d08f044c439ce86a2d6fcca57b
(4, 34784)
6 4f545737bf3347fbbc9af60b0be9a963
(4, 34720)
7 7626dde27d604ac28a0240bdd54eba7a
(4, 34720)
8 be99ffc878b24aca8956bbb4e0f97d0c
(4, 34688)
9 9813c23a5f1448b09bb7910fea9baf20
(4, 34688)
10 023c4df2d451409881d8e6ea82f14704
(4, 34688)
11 c235638ed66145988d17f9d0601923f2
(4, 34720)
12 bc3c8a953f6b4dcdb77b521d89f3d9d5
(4, 34688)
13 1e3d79dae62742a0ad64c91679863358
(4, 34752)
14 2afb9d32310e4546a71cbe432911eca2
(4, 34752)
15 cd21dbfc3bd749c7b10a5c42562e0c42
(4, 34784)
16 88449a5cb1644a199c1c11f6ac034867
(4, 34784)
17 2ff86dc19c4644a1a88ce5ba848f56e5
(4, 34752)
18 bf2938e43c6f487497cda76b51bfc406
(4, 34688)
19 b26e791522294bec90f86fd72226e35c
(4, 34688)
20 c844bf5a9f2243ff8f4bf2c85fe218ff
(4, 34688)
21 fedfb3a6cb804635a0f47143f9ca8d6f
(4, 34720)
22 965f6af5

In [54]:
lidar_top_data

{'token': 'faa171b7a8164f4cbf90b260af5c27f1',
 'sample_token': '29e056fc277543c9bc42310b122c640e',
 'ego_pose_token': 'faa171b7a8164f4cbf90b260af5c27f1',
 'calibrated_sensor_token': 'a183049901c24361a6b0b11b8013137c',
 'timestamp': 1532402946297085,
 'fileformat': 'pcd',
 'is_key_frame': True,
 'height': 0,
 'width': 0,
 'filename': 'samples/LIDAR_TOP/n015-2018-07-24-11-22-45+0800__LIDAR_TOP__1532402946297085.pcd.bin',
 'prev': '33052d8527a544f49cb82a2c31cc2e5e',
 'next': 'f3f638b73c68443f9fd893a9d8025e44',
 'sensor_modality': 'lidar',
 'channel': 'LIDAR_TOP'}

In [75]:
getattr()

KeyError: 'f3f638b73c68443f9fd893a9d8025e44'

In [71]:
pc_file, d, d2 = nusc.get_sample_data(lidar_top_data['token'])
d[0]

label: nan, score: nan, xyz: [-12.47, -52.33, -1.92], wlh: [0.62, 0.67, 1.64], rot axis: [0.04, 0.01, 1.00], ang(degrees): 84.52, ang(rad): 1.48, vel: nan, nan, nan, name: human.pedestrian.adult, token: 93d5b79041c64693a5b32f1103a39a06

In [48]:
my_scene = nusc.scene[0]
first_sample_token = my_scene['first_sample_token']
last_sample_token = my_scene['last_sample_token']

token = first_sample_token
count = 0
while(token != last_sample_token):
    my_sample = nusc.get('sample', token)
    
    lidar_top_data = nusc.get('sample_data', my_sample['data']['LIDAR_TOP'])
    pcl_path = os.path.join(nusc.dataroot, lidar_top_data['filename'])

    pc = LidarPointCloud.from_file(pcl_path)
    print(pc.points.shape)

    token = my_sample['next']
    count+=1
    print(count, token)


(4, 34688)
1 39586f9d59004284a7114a68825e8eec
(4, 34720)
2 356d81f38dd9473ba590f39e266f54e5
(4, 34720)
3 e0845f5322254dafadbbed75aaa07969
(4, 34688)
4 c923fe08b2ff4e27975d2bf30934383b
(4, 34752)
5 f1e3d9d08f044c439ce86a2d6fcca57b
(4, 34784)
6 4f545737bf3347fbbc9af60b0be9a963
(4, 34720)
7 7626dde27d604ac28a0240bdd54eba7a
(4, 34720)
8 be99ffc878b24aca8956bbb4e0f97d0c
(4, 34688)
9 9813c23a5f1448b09bb7910fea9baf20
(4, 34688)
10 023c4df2d451409881d8e6ea82f14704
(4, 34688)
11 c235638ed66145988d17f9d0601923f2
(4, 34720)
12 bc3c8a953f6b4dcdb77b521d89f3d9d5
(4, 34688)
13 1e3d79dae62742a0ad64c91679863358
(4, 34752)
14 2afb9d32310e4546a71cbe432911eca2
(4, 34752)
15 cd21dbfc3bd749c7b10a5c42562e0c42
(4, 34784)
16 88449a5cb1644a199c1c11f6ac034867
(4, 34784)
17 2ff86dc19c4644a1a88ce5ba848f56e5
(4, 34752)
18 bf2938e43c6f487497cda76b51bfc406
(4, 34688)
19 b26e791522294bec90f86fd72226e35c
(4, 34688)
20 c844bf5a9f2243ff8f4bf2c85fe218ff
(4, 34688)
21 fedfb3a6cb804635a0f47143f9ca8d6f
(4, 34720)
22 965f6af5

In [72]:
sample = nusc.sample[0]
pcl, _ = LidarPointCloud.from_file_multisweep(nusc, sample, 'LIDAR_TOP', 'LIDAR_TOP', nsweeps=10)
print(pcl.points.T.dtype)

float32


In [76]:
lidar_top_data

{'token': 'faa171b7a8164f4cbf90b260af5c27f1',
 'sample_token': '29e056fc277543c9bc42310b122c640e',
 'ego_pose_token': 'faa171b7a8164f4cbf90b260af5c27f1',
 'calibrated_sensor_token': 'a183049901c24361a6b0b11b8013137c',
 'timestamp': 1532402946297085,
 'fileformat': 'pcd',
 'is_key_frame': True,
 'height': 0,
 'width': 0,
 'filename': 'samples/LIDAR_TOP/n015-2018-07-24-11-22-45+0800__LIDAR_TOP__1532402946297085.pcd.bin',
 'prev': '33052d8527a544f49cb82a2c31cc2e5e',
 'next': 'f3f638b73c68443f9fd893a9d8025e44',
 'sensor_modality': 'lidar',
 'channel': 'LIDAR_TOP'}

In [122]:
my_scene = nusc.scene[0]
first_sample_token = my_scene['first_sample_token']
last_sample_token = my_scene['last_sample_token']

sample_rec = nusc.get('sample', last_sample_token)
last_time = sample_rec['timestamp']

sample_rec = nusc.get('sample', first_sample_token)
first_time = sample_rec['timestamp']

ref_sd_token = sample_rec['data']['LIDAR_TOP']
ref_sd_rec = nusc.get('sample_data', ref_sd_token)
ref_pose_rec = nusc.get('ego_pose', ref_sd_rec['ego_pose_token'])
ref_cs_rec = nusc.get('calibrated_sensor', ref_sd_rec['calibrated_sensor_token'])
ref_time = 1e-6 * ref_sd_rec['timestamp']

# Homogeneous transform from ego car frame to reference frame.
ref_from_car = transform_matrix(ref_cs_rec['translation'], Quaternion(ref_cs_rec['rotation']), inverse=True)

# Homogeneous transformation matrix from global to _current_ ego car frame.
car_from_global = transform_matrix(ref_pose_rec['translation'], Quaternion(ref_pose_rec['rotation']),
                                   inverse=True)

sample_data_token = sample_rec['data']['LIDAR_TOP']
current_sd_rec = nusc.get('sample_data', sample_data_token)

print(last_time - first_time)
for i in range(1000):
    print(f"{i} : {current_sd_rec['timestamp'] - first_time}")
    current_pc = LidarPointCloud.from_file(os.path.join(nusc.dataroot, current_sd_rec['filename']))

    current_pose_rec = nusc.get("ego_pose", current_sd_rec['ego_pose_token'])
    global_from_car = transform_matrix(current_pose_rec['translation'], Quaternion(current_pose_rec['rotation']), inverse = False)

    current_cs_rec = nusc.get('calibrated_sensor', current_sd_rec['calibrated_sensor_token'])
    car_from_current = transform_matrix(current_cs_rec['translation'], Quaternion(current_cs_rec['rotation']), inverse =False)

    trans_matrix = reduce(np.dot, [ref_from_car, car_from_global, global_from_car, car_from_current])
    current_pc.transform(trans_matrix)

    if current_sd_rec['next'] == "":
        break
    else:
        current_sd_rec = nusc.get('sample_data', current_sd_rec['next'])

19149566
0 : 0
1 : 49801
2 : 99538
3 : 149855
4 : 200646
5 : 249949
6 : 299707
7 : 350030
8 : 399828
9 : 450112
10 : 499896
11 : 549662
12 : 599963
13 : 649736
14 : 700046
15 : 752608
16 : 800143
17 : 849930
18 : 899682
19 : 950008
20 : 999752
21 : 1050097
22 : 1099889
23 : 1149605
24 : 1199933
25 : 1249710
26 : 1299503
27 : 1349778
28 : 1399549
29 : 1449863
30 : 1499642
31 : 1549402
32 : 1599733
33 : 1649494
34 : 1699833
35 : 1749581
36 : 1799354
37 : 1849678
38 : 1899457
39 : 1949744
40 : 1999517
41 : 2049846
42 : 2099609
43 : 2149917
44 : 2199705
45 : 2250000
46 : 2300324
47 : 2350082
48 : 2400429
49 : 2450169
50 : 2504650
51 : 2550260
52 : 2600600
53 : 2650335
54 : 2700868
55 : 2750433
56 : 2800746
57 : 2850523
58 : 2900289
59 : 2950590
60 : 3000374
61 : 3050713
62 : 3100445
63 : 3150232
64 : 3200528
65 : 3250339
66 : 3300628
67 : 3350430
68 : 3400178
69 : 3450534
70 : 3500257
71 : 3550560
72 : 3600341
73 : 3650120
74 : 3700432
75 : 3750193
76 : 3800513
77 : 3850276
78 : 3900042
79

# Map

In [135]:
nusc_map = NuScenesMap(dataroot='./data/sets/nuscenes', map_name='singapore-onenorth')

In [139]:
my_scene = nusc.scene[0]
first_sample_token = my_scene['first_sample_token']
last_sample_token = my_scene['last_sample_token']

sample_rec = nusc.get('sample', last_sample_token)
last_time = sample_rec['timestamp']

sample_rec = nusc.get('sample', first_sample_token)
first_time = sample_rec['timestamp']

ref_sd_token = sample_rec['data']['LIDAR_TOP']
ref_sd_rec = nusc.get('sample_data', ref_sd_token)
ref_pose_rec = nusc.get('ego_pose', ref_sd_rec['ego_pose_token'])
ref_cs_rec = nusc.get('calibrated_sensor', ref_sd_rec['calibrated_sensor_token'])
ref_time = 1e-6 * ref_sd_rec['timestamp']

# Homogeneous transform from ego car frame to reference frame.
ref_from_car = transform_matrix(ref_cs_rec['translation'], Quaternion(ref_cs_rec['rotation']), inverse=True)

# Homogeneous transformation matrix from global to _current_ ego car frame.
car_from_global = transform_matrix(ref_pose_rec['translation'], Quaternion(ref_pose_rec['rotation']),
                                   inverse=True)

sample_data_token = sample_rec['data']['LIDAR_TOP']
current_sd_rec = nusc.get('sample_data', sample_data_token)

print(last_time - first_time)
for i in range(1000):
    print(f"{i} : {current_sd_rec['timestamp'] - first_time}")
    current_pc = LidarPointCloud.from_file(os.path.join(nusc.dataroot, current_sd_rec['filename']))

    current_pose_rec = nusc.get("ego_pose", current_sd_rec['ego_pose_token'])
    global_from_car = transform_matrix(current_pose_rec['translation'], Quaternion(current_pose_rec['rotation']), inverse = False)

    lane = nusc_map.get_closest_lane(current_pose_rec['translation'][0], current_pose_rec['translation'][1])
    nusc_map.
    print(lane)
    if current_sd_rec['next'] == "":
        break
    else:
        current_sd_rec = nusc.get('sample_data', current_sd_rec['next'])

19149566
0 : 0
91da635c-b931-4517-89c9-ff90792d75f0
1 : 49801
91da635c-b931-4517-89c9-ff90792d75f0
2 : 99538
91da635c-b931-4517-89c9-ff90792d75f0
3 : 149855
91da635c-b931-4517-89c9-ff90792d75f0
4 : 200646
91da635c-b931-4517-89c9-ff90792d75f0
5 : 249949
91da635c-b931-4517-89c9-ff90792d75f0
6 : 299707
91da635c-b931-4517-89c9-ff90792d75f0
7 : 350030
91da635c-b931-4517-89c9-ff90792d75f0
8 : 399828
91da635c-b931-4517-89c9-ff90792d75f0
9 : 450112
91da635c-b931-4517-89c9-ff90792d75f0
10 : 499896
91da635c-b931-4517-89c9-ff90792d75f0
11 : 549662
91da635c-b931-4517-89c9-ff90792d75f0
12 : 599963
91da635c-b931-4517-89c9-ff90792d75f0
13 : 649736
91da635c-b931-4517-89c9-ff90792d75f0
14 : 700046
91da635c-b931-4517-89c9-ff90792d75f0
15 : 752608
91da635c-b931-4517-89c9-ff90792d75f0
16 : 800143
91da635c-b931-4517-89c9-ff90792d75f0
17 : 849930
91da635c-b931-4517-89c9-ff90792d75f0
18 : 899682
91da635c-b931-4517-89c9-ff90792d75f0
19 : 950008
8f74cf95-642c-4683-abd0-b7f661ba7fbd
20 : 999752
8f74cf95-642c-46

1d461032-cf3a-48dc-aad2-181704fd63f9
165 : 8300484
1d461032-cf3a-48dc-aad2-181704fd63f9
166 : 8350838
1d461032-cf3a-48dc-aad2-181704fd63f9
167 : 8400575
1d461032-cf3a-48dc-aad2-181704fd63f9
168 : 8450908
1d461032-cf3a-48dc-aad2-181704fd63f9
169 : 8501296
1d461032-cf3a-48dc-aad2-181704fd63f9
170 : 8551011
1d461032-cf3a-48dc-aad2-181704fd63f9
171 : 8601302
1d461032-cf3a-48dc-aad2-181704fd63f9
172 : 8651077
1d461032-cf3a-48dc-aad2-181704fd63f9
173 : 8701394
1d461032-cf3a-48dc-aad2-181704fd63f9
174 : 8751186
1d461032-cf3a-48dc-aad2-181704fd63f9
175 : 8801487
1d461032-cf3a-48dc-aad2-181704fd63f9
176 : 8851239
1d461032-cf3a-48dc-aad2-181704fd63f9
177 : 8901017
1d461032-cf3a-48dc-aad2-181704fd63f9
178 : 8951344
1d461032-cf3a-48dc-aad2-181704fd63f9
179 : 9001139
1d461032-cf3a-48dc-aad2-181704fd63f9
180 : 9051408
1d461032-cf3a-48dc-aad2-181704fd63f9
181 : 9101199
1d461032-cf3a-48dc-aad2-181704fd63f9
182 : 9150937
1d461032-cf3a-48dc-aad2-181704fd63f9
183 : 9201277
1d461032-cf3a-48dc-aad2-181704f

Exception ignored in: <bound method BaseGeometry.__del__ of <shapely.geometry.polygon.Polygon object at 0x000002C2435BC5C0>>
Traceback (most recent call last):
  File "D:\Sangwons_Room\00_SoftWares\Anaconda\envs\torch\lib\site-packages\shapely\geometry\base.py", line 242, in __del__
    self.empty(val=None)
  File "D:\Sangwons_Room\00_SoftWares\Anaconda\envs\torch\lib\site-packages\shapely\geometry\base.py", line 227, in empty
    self._lgeos.GEOSGeom_destroy(self.__geom__)
KeyboardInterrupt: 


bfdbd392-4753-485b-96a7-f26ed396ccba
278 : 13949544
bfdbd392-4753-485b-96a7-f26ed396ccba
279 : 13999297
9b76cd1e-5d2e-4848-b4e8-16681d8a4f14
280 : 14049631
bfdbd392-4753-485b-96a7-f26ed396ccba
281 : 14099375
bfdbd392-4753-485b-96a7-f26ed396ccba
282 : 14149702
9b76cd1e-5d2e-4848-b4e8-16681d8a4f14
283 : 14199463
9b76cd1e-5d2e-4848-b4e8-16681d8a4f14
284 : 14249785
bfdbd392-4753-485b-96a7-f26ed396ccba
285 : 14299573
bfdbd392-4753-485b-96a7-f26ed396ccba
286 : 14349320
9b76cd1e-5d2e-4848-b4e8-16681d8a4f14
287 : 14399647
9b76cd1e-5d2e-4848-b4e8-16681d8a4f14
288 : 14450335
9b76cd1e-5d2e-4848-b4e8-16681d8a4f14
289 : 14499735
bfdbd392-4753-485b-96a7-f26ed396ccba
290 : 14549512
bfdbd392-4753-485b-96a7-f26ed396ccba
291 : 14599304
bfdbd392-4753-485b-96a7-f26ed396ccba
292 : 14649582
5e73e2b0-3c82-4124-a405-fecff46c2d25
293 : 14699345
5e73e2b0-3c82-4124-a405-fecff46c2d25
294 : 14749664
5e73e2b0-3c82-4124-a405-fecff46c2d25
295 : 14799445
5e73e2b0-3c82-4124-a405-fecff46c2d25
296 : 14849753
5e73e2b0-3c8

Exception ignored in: <bound method BaseGeometry.__del__ of <shapely.geometry.polygon.Polygon object at 0x000002C2435BC7F0>>
Traceback (most recent call last):
  File "D:\Sangwons_Room\00_SoftWares\Anaconda\envs\torch\lib\site-packages\shapely\geometry\base.py", line 242, in __del__
    self.empty(val=None)
  File "D:\Sangwons_Room\00_SoftWares\Anaconda\envs\torch\lib\site-packages\shapely\geometry\base.py", line 227, in empty
    self._lgeos.GEOSGeom_destroy(self.__geom__)
KeyboardInterrupt: 


5e73e2b0-3c82-4124-a405-fecff46c2d25
354 : 17748932
5e73e2b0-3c82-4124-a405-fecff46c2d25
355 : 17799250
5e73e2b0-3c82-4124-a405-fecff46c2d25
356 : 17849009
5e73e2b0-3c82-4124-a405-fecff46c2d25
357 : 17899329
5e73e2b0-3c82-4124-a405-fecff46c2d25
358 : 17949094
5e73e2b0-3c82-4124-a405-fecff46c2d25
359 : 17999413
5e73e2b0-3c82-4124-a405-fecff46c2d25
360 : 18049197
5e73e2b0-3c82-4124-a405-fecff46c2d25
361 : 18098948
5e73e2b0-3c82-4124-a405-fecff46c2d25
362 : 18149259
5e73e2b0-3c82-4124-a405-fecff46c2d25
363 : 18199033
5e73e2b0-3c82-4124-a405-fecff46c2d25
364 : 18249352
dab7c5c2-8558-483c-9c8c-31815fbf2898
365 : 18299121
dab7c5c2-8558-483c-9c8c-31815fbf2898
366 : 18349435
dab7c5c2-8558-483c-9c8c-31815fbf2898
367 : 18399195
dab7c5c2-8558-483c-9c8c-31815fbf2898
368 : 18448975
dab7c5c2-8558-483c-9c8c-31815fbf2898
369 : 18499361
dab7c5c2-8558-483c-9c8c-31815fbf2898
370 : 18549081
1ba067c9-a69c-4cd1-bc3c-8bdc9daec466
371 : 18599374
1ba067c9-a69c-4cd1-bc3c-8bdc9daec466
372 : 18649134
1ba067c9-a69

In [140]:
nusc_map.__dir__()

['dataroot',
 'map_name',
 'geometric_layers',
 'non_geometric_polygon_layers',
 'lookup_polygon_layers',
 'non_geometric_line_layers',
 'non_geometric_layers',
 'layer_names',
 'json_fname',
 'json_obj',
 'version',
 'canvas_edge',
 'polygon',
 'line',
 'node',
 'drivable_area',
 'road_segment',
 'road_block',
 'lane',
 'ped_crossing',
 'walkway',
 'stop_line',
 'carpark_area',
 'road_divider',
 'lane_divider',
 'traffic_light',
 'arcline_path_3',
 'connectivity',
 'lane_connector',
 '_token2ind',
 'explorer',
 '__module__',
 '__doc__',
 '__init__',
 '_load_layer',
 '_load_layer_dict',
 '_load_layers',
 '_make_token2ind',
 '_make_shortcuts',
 '_get_stop_line_cue',
 'get',
 'getind',
 'render_record',
 'render_layers',
 'render_map_patch',
 'render_map_in_image',
 'render_egoposes_on_fancy_map',
 'render_centerlines',
 'render_map_mask',
 'get_map_mask',
 'get_map_geom',
 'get_records_in_patch',
 'is_record_in_patch',
 'layers_on_point',
 'record_on_point',
 'extract_polygon',
 'extrac